<a href="https://colab.research.google.com/github/liam-10beauty/workstation_config/blob/gist_xfer/range_of_motion_new_gantry.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#@title Install dependency and import needed packages
!pip install dash numpy-stl

import numpy as np

import plotly.express as px
import plotly.graph_objects as go

import dash
import dash_core_components as dcc
import dash_html_components as html
from stl import mesh

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.4/10.4 MB 39.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.6/233.6 kB 19.7 MB/s eta 0:00:00
  Attempting uninstall: Werkzeug
    Found existing installation: Werkzeug 2.3.7
    Uninstalling Werkzeug-2.3.7:
      Successfully uninstalled Werkzeug-2.3.7


<ipython-input-1-4a3d328888b8>:10: UserWarning: 
The dash_core_components package is deprecated. Please replace
`import dash_core_components as dcc` with `from dash import dcc`
  import dash_core_components as dcc
<ipython-input-1-4a3d328888b8>:11: UserWarning: 
The dash_html_components package is deprecated. Please replace
`import dash_html_components as html` with `from dash import html`
  import dash_html_components as html


In [ ]:
#@title Mount drive, locate json files
from google.colab import drive

drive.mount('/content/gdrive', force_remount=True)


Mounted at /content/gdrive


In [ ]:
# optionally clear google drive cache to load updated files
!google-drive-ocamlfuse -cc

/bin/bash: line 1: google-drive-ocamlfuse: command not found


In [ ]:
#@title define the path files to load - G2 or Alpha
path_drive_path = '/content/gdrive/Shared drives/10Beauty/Development/Phase 4: Product Development/Software/Data/gantry_range_of_motion/'
datasets = {}
datasets['G2'] = {}
datasets['G2']['application'] = path_drive_path + 'application_path.json'
datasets['G2']['removal'] = path_drive_path + 'removal_path.json'
datasets['G2']['shaping'] = path_drive_path + 'shaping_path.json'
datasets['G2']['cuticle'] = path_drive_path + 'cuticle_path.json'
datasets['G2']['p_idm_0'] = [15.577, 0.71079863, 25.82342889, 0., 0.]

datasets['Alpha'] = {}
datasets['Alpha']['application'] = path_drive_path + 'alpha_large_nail_paths/application_path_no_area.json'
datasets['Alpha']['removal'] = path_drive_path + 'alpha_large_nail_paths/removal_path.json'
datasets['Alpha']['shaping'] = path_drive_path + 'alpha_large_nail_paths/shaping_path.json'
datasets['Alpha']['cuticle'] = path_drive_path + 'alpha_large_nail_paths/cuticle_path.json'
datasets['Alpha']['p_idm_0'] = [0.0, 0.0, 0.0, 0., 0.]


In [ ]:
#@title Choose which dataset to visualize, options: 'G2' or 'Alpha'
dataset_name = 'Alpha'

# Turning off stl output for now since it's not needed
output_stl = False

In [ ]:
#@title Define function that exports stl file

def export_to_stl(vertices, faces, stl_filename):
    # EXAMPLE: Define the 8 vertices of the cube
    # vertices = np.array([\
    #     [-1, -1, -1],
    #     [+1, -1, -1],
    #     [+1, +1, -1],
    #     [-1, +1, -1],
    #     [-1, -1, +1],
    #     [+1, -1, +1],
    #     [+1, +1, +1],
    #     [-1, +1, +1]])
    # # Define the 12 triangles composing the cube
    # faces = np.array([\
    #     [0,3,1],
    #     [1,3,2],
    #     [0,4,7],
    #     [0,7,3],
    #     [4,5,6],
    #     [4,6,7],
    #     [5,1,2],
    #     [5,2,6],
    #     [2,3,6],
    #     [3,7,6],
    #     [0,1,5],
    #     [0,5,4]])

    # Create the mesh
    mesh_stl = mesh.Mesh(np.zeros(faces.shape[0], dtype=mesh.Mesh.dtype))
    for i, f in enumerate(faces):
        for j in range(3):
            mesh_stl.vectors[i][j] = vertices[f[j],:]

    mesh_stl.save(stl_filename)

In [ ]:
  #@title Define function for visualization

  def visualize_path(x_mm, y_mm, z_mm, theta_rad, phi_rad, stl_outupt=False, stl_filename="na.stl",p_idm_0=None):
    # Compensate for calibration tool offset (shaping tool in this case...)
    # and the angle in y axis
    y_tilt_angle = 10.0 / 180.0 * np.pi

    if p_idm_0 is None:
      p_idm_0 = [-23.9, -1.219, 40.3, 0., 0.]
    x_ref = np.array(x_mm) + p_idm_0[0]
    y_ref = np.array(y_mm) * np.cos(y_tilt_angle) + p_idm_0[1]
    z_ref = np.array(z_mm) - np.array(y_mm) * np.sin(y_tilt_angle) + p_idm_0[2]

    data_list = [go.Scatter3d(x=x_ref, y=y_ref, z=z_ref,
                      mode='markers',
                      marker=dict(size=5)
                      )]

    print("Gantry X range: [{}, {}]".format(min(x_ref), max(x_ref)))
    print("Gantry Y range: [{}, {}]".format(min(y_ref), max(y_ref)))
    print("Gantry Z range: [{}, {}]".format(min(z_ref), max(z_ref)))
    print("Gantry THETA range: [{}, {}]".format(min(theta_rad), max(theta_rad)))
    print("Gantry PHI range: [{}, {}]".format(min(phi_rad), max(phi_rad)))

    # define boxes that sort of show the machine geometry
    ts_theta_offset = 47.66
    ts_plate_to_motor_length = 76.08

    theta_box_x = 66 #mm
    theta_box_y = ts_plate_to_motor_length #mm
    theta_box_z = 56 #mm
    theta_box_x_min = -theta_box_x/2 #mm
    theta_box_y_min = ts_theta_offset #mm
    theta_box_z_min = -theta_box_z/2 #mm


    theta_box_corners = np.array([[theta_box_x_min+theta_box_x, theta_box_y_min+theta_box_y, theta_box_z_min],
                                [theta_box_x_min, theta_box_y_min+theta_box_y, theta_box_z_min],
                                [theta_box_x_min, theta_box_y_min, theta_box_z_min],
                                [theta_box_x_min+theta_box_x, theta_box_y_min, theta_box_z_min],
                                [theta_box_x_min+theta_box_x, theta_box_y_min+theta_box_y, theta_box_z_min+theta_box_z],
                                [theta_box_x_min, theta_box_y_min+theta_box_y, theta_box_z_min+theta_box_z],
                                [theta_box_x_min, theta_box_y_min, theta_box_z_min+theta_box_z],
                                [theta_box_x_min+theta_box_x, theta_box_y_min, theta_box_z_min+theta_box_z]]).T

    # original theta box code from Lu
    # theta_box_z_bottom = -5.0 # mm
    # theta_box_corners = np.array([[theta_box_w*0.5, theta_box_l*0.5, theta_box_z_bottom],
    #                             [-theta_box_w*0.5, theta_box_l*0.5, theta_box_z_bottom],
    #                             [-theta_box_w*0.5, -theta_box_l*0.5, theta_box_z_bottom],
    #                             [theta_box_w*0.5, -theta_box_l*0.5, theta_box_z_bottom],
    #                             [theta_box_w*0.5, theta_box_l*0.5, theta_box_z_bottom+theta_box_h],
    #                             [-theta_box_w*0.5, theta_box_l*0.5, theta_box_z_bottom+theta_box_h],
    #                             [-theta_box_w*0.5, -theta_box_l*0.5, theta_box_z_bottom+theta_box_h],
    #                             [theta_box_w*0.5, -theta_box_l*0.5, theta_box_z_bottom+theta_box_h]]).T

    # print("theta_box_corners shape = {}".format(theta_box_corners.shape))

    # #zbox1 theta bracket
    z_box1_x = 55.0
    z_box1_y = 141.47
    z_box1_z = 50.43
    z_box1_x_min = -27.5
    z_box1_y_min = -30.72
    z_box1_z_min = 85.68

    # #zbox2 z carriage
    z_box2_x = 70.0
    z_box2_y = 40.20
    z_box2_z = 173.0
    z_box2_x_min = -35.0
    z_box2_y_min = 76.30
    z_box2_z_min = 84.49 #fixed distance from top of the screw hole in the aluminum block


    zbox1_corners = np.array([[z_box1_x_min+z_box1_x, z_box1_y_min+z_box1_y, z_box1_z_min],
                                [z_box1_x_min, z_box1_y_min+z_box1_y, z_box1_z_min],
                                [z_box1_x_min, z_box1_y_min, z_box1_z_min],
                                [z_box1_x_min+z_box1_x, z_box1_y_min, z_box1_z_min],
                                [z_box1_x_min+z_box1_x, z_box1_y_min+z_box1_y, z_box1_z_min+z_box1_z],
                                [z_box1_x_min, z_box1_y_min+z_box1_y, z_box1_z_min+z_box1_z],
                                [z_box1_x_min, z_box1_y_min, z_box1_z_min+z_box1_z],
                                [z_box1_x_min+z_box1_x, z_box1_y_min, z_box1_z_min+z_box1_z]]).T


    zbox2_corners = np.array([[z_box2_x_min+z_box2_x, z_box2_y_min+z_box2_y, z_box2_z_min],
                                [z_box2_x_min, z_box2_y_min+z_box2_y, z_box2_z_min],
                                [z_box2_x_min, z_box2_y_min, z_box2_z_min],
                                [z_box2_x_min+z_box2_x, z_box2_y_min, z_box2_z_min],
                                [z_box2_x_min+z_box2_x, z_box2_y_min+z_box2_y, z_box2_z_min+z_box2_z],
                                [z_box2_x_min, z_box2_y_min+z_box2_y, z_box2_z_min+z_box2_z],
                                [z_box2_x_min, z_box2_y_min, z_box2_z_min+z_box2_z],
                                [z_box2_x_min+z_box2_x, z_box2_y_min, z_box2_z_min+z_box2_z]]).T

#MVP tool swap + tools
######################################################

    #ts_theta_offset = 20 #defined in theta box
    # ts_plate_to_motor_length = 95.03 #defined in theta box
    application_y = 63.87
    shaping_y = 41.95
    cuticle_y = 37.5
    removal_y = 57.0

    # #shaping Alpha
    # phi_box_x = 65.0
    # phi_box_y = ts_plate_to_motor_length + shaping_y
    # phi_box_z = 57.10
    # phi_box_x_min = -46.30
    # phi_box_y_min = ts_theta_offset - shaping_y
    # phi_box_z_min = -57.10/2

    # #removal Alpha
    # phi_box_x = 32.80
    # phi_box_y = ts_plate_to_motor_length + removal_y
    # phi_box_z = 57.0
    # phi_box_x_min = -31.0
    # phi_box_y_min = ts_theta_offset - removal_y
    # phi_box_z_min = -41.0

    # #application Alpha
    # phi_box_x = 59.45
    # phi_box_y = ts_plate_to_motor_length + application_y
    # phi_box_z = 57.10
    # phi_box_x_min = -31.0
    # phi_box_y_min = ts_theta_offset - application_y
    # phi_box_z_min = -57.10/2

    #cuticle MVP
    phi_box_x = 25
    phi_box_y = 64 #ts_plate_to_motor_length #+ cuticle_y
    phi_box_z = 25
    phi_box_x_min = -phi_box_x/2
    phi_box_y_min = -16.57 #- cuticle_y
    phi_box_z_min = -phi_box_z/2

#######################################################


#Alpha horizontal tool swap + tools
######################################################

    #ts_theta_offset = 20 #defined in theta box
    # ts_plate_to_motor_length = 95.03 #defined in theta box
    #application_y = 63.87
    #shaping_y = 41.95
    #cuticle_y = 37.5
    #removal_y = 57.0

    # #shaping Alpha
    # phi_box_x = 65.0
    # phi_box_y = ts_plate_to_motor_length + shaping_y
    # phi_box_z = 57.10
    # phi_box_x_min = -46.30
    # phi_box_y_min = ts_theta_offset - shaping_y
    # phi_box_z_min = -57.10/2

    # #removal Alpha
    # phi_box_x = 32.80
    # phi_box_y = ts_plate_to_motor_length + removal_y
    # phi_box_z = 57.0
    # phi_box_x_min = -31.0
    # phi_box_y_min = ts_theta_offset - removal_y
    # phi_box_z_min = -41.0

    # #application Alpha
    # phi_box_x = 59.45
    # phi_box_y = ts_plate_to_motor_length + application_y
    # phi_box_z = 57.10
    # phi_box_x_min = -31.0
    # phi_box_y_min = ts_theta_offset - application_y
    # phi_box_z_min = -57.10/2

    #cuticle Alpha
    #phi_box_x = 66
    #phi_box_y = ts_plate_to_motor_length #+ cuticle_y
    #phi_box_z = 56
    #phi_box_x_min = -phi_box_x/2
    #phi_box_y_min = ts_theta_offset #- cuticle_y
    #phi_box_z_min = -phi_box_z/2

#######################################################


#Gantry 2 vertical tool swap + tools
######################################################

    # # #shaping G2
    # phi_box_x = 110.63
    # phi_box_y = 47.84
    # phi_box_z = 48.86
    # phi_box_x_min = -35.30
    # phi_box_y_min = -38.19
    # phi_box_z_min = -26.32

    # #removal G2
    # phi_box_x = 85.91
    # phi_box_y = 62.93
    # phi_box_z = 65.18
    # phi_box_x_min = -10.58
    # phi_box_y_min = -53.28
    # phi_box_z_min = -25.0

    # #application G2
    # phi_box_x = 97.83
    # phi_box_y = 78.17
    # phi_box_z = 47.54
    # phi_box_x_min = -22.5
    # phi_box_y_min = -68.52
    # phi_box_z_min = -25.0

    # #cuticle G2
    # phi_box_x = 116.17
    # phi_box_y = 44.36
    # phi_box_z = 47.54
    # phi_box_x_min = -40.84
    # phi_box_y_min = -34.71
    # phi_box_z_min = -25.0

#######################################################

    phi_box_corners = np.array([[phi_box_x_min+phi_box_x, phi_box_y_min+phi_box_y, phi_box_z_min],
                                [phi_box_x_min, phi_box_y_min+phi_box_y, phi_box_z_min],
                                [phi_box_x_min, phi_box_y_min, phi_box_z_min],
                                [phi_box_x_min+phi_box_x, phi_box_y_min, phi_box_z_min],
                                [phi_box_x_min+phi_box_x, phi_box_y_min+phi_box_y, phi_box_z_min+phi_box_z],
                                [phi_box_x_min, phi_box_y_min+phi_box_y, phi_box_z_min+phi_box_z],
                                [phi_box_x_min, phi_box_y_min, phi_box_z_min+phi_box_z],
                                [phi_box_x_min+phi_box_x, phi_box_y_min, phi_box_z_min+phi_box_z]]).T

    # original phi box code from Lu
    # phi_box_width = 45.0
    # phi_box_length = 40.0
    # phi_box_height = 20.0
    # phi_box_x_min = -35.0
    # phi_box_z_bottom = -10.0
    # phi_box_corners = np.array([[phi_box_x_min, 0.0+0.5*phi_box_width, phi_box_z_bottom],
    #                             [phi_box_x_min, 0.0-0.5*phi_box_width, phi_box_z_bottom],
    #                             [phi_box_x_min+phi_box_length, 0.0-0.5*phi_box_width, phi_box_z_bottom],
    #                             [phi_box_x_min+phi_box_length, 0.0+0.5*phi_box_width, phi_box_z_bottom],
    #                             [phi_box_x_min, 0.0+0.5*phi_box_width, phi_box_z_bottom+phi_box_height],
    #                             [phi_box_x_min, 0.0-0.5*phi_box_width, phi_box_z_bottom+phi_box_height],
    #                             [phi_box_x_min+phi_box_length, 0.0-0.5*phi_box_width, phi_box_z_bottom+phi_box_height],
    #                             [phi_box_x_min+phi_box_length, 0.0+0.5*phi_box_width, phi_box_z_bottom+phi_box_height]]).T
    # print("phi_box_corners = {}".format(phi_box_corners))

    counter = 0
    y_tilt_angle = 10.0 / 180.0 * np.pi # radian

    vertices_list = None
    faces_list = None
    for x,y,z,theta,phi in zip(x_ref, y_ref, z_ref, theta_rad, phi_rad):
        # print("({},{},{},{},{})".format(x,y,z,theta,phi))
        # Adding the box representing the machine for each configuration on the path
        # theta_box_center_x = x
        # theta_box_center_y = y
        # theta_box_center_z = z + 20.0

        sin_theta = np.sin(theta)
        cos_theta = np.cos(theta)

        theta_rot_matrix = np.array([[cos_theta, -sin_theta, 0],
                                   [sin_theta, cos_theta, 0],
                                   [0, 0, 1]])
        # theta_box_a = [theta_box_center_x - theta_box_y*0.5*sin_theta + theta_box_x*0.5*cos_theta,
        #                theta_box_center_y + theta_box_y*0.5*cos_theta + theta_box_x*0.5*sin_theta,
        #                theta_box_center_z - theta_box_z*0.5]
        # theta_box_b = [theta_box_center_x - theta_box_y*0.5*sin_theta - theta_box_x*0.5*cos_theta,
        #                theta_box_center_y + theta_box_y*0.5*cos_theta - theta_box_x*0.5*sin_theta,
        #                theta_box_center_z - theta_box_z*0.5]
        # theta_box_c = [theta_box_center_x + theta_box_y*0.5*sin_theta - theta_box_x*0.5*cos_theta,
        #                theta_box_center_y - theta_box_y*0.5*cos_theta - theta_box_x*0.5*sin_theta,
        #                theta_box_center_z - theta_box_z*0.5]
        # theta_box_d = [theta_box_center_x + theta_box_y*0.5*sin_theta + theta_box_x*0.5*cos_theta,
        #                theta_box_center_y - theta_box_y*0.5*cos_theta + theta_box_x*0.5*sin_theta,
        #                theta_box_center_z - theta_box_z*0.5]

        # print("theta_box = {},{},{},{}".format(theta_box_a, theta_box_b, theta_box_c, theta_box_d))

        theta_box_final = np.matmul(theta_rot_matrix, theta_box_corners) + np.tile(np.array([x, y, z]), [8,1]).T

        # print("theta_box_final = {}".format(theta_box_final))
        # print("{}".format(theta_box_final))

        sin_phi = np.sin(phi)
        cos_phi = np.cos(phi)

        phi_rot_matrix = np.array([[cos_phi, 0, -sin_phi],
                                   [0, 1, 0],
                                   [sin_phi, 0, cos_phi]])

        phi_box_after_phi_rot =  np.matmul(phi_rot_matrix, phi_box_corners)
        phi_box_final = np.matmul(theta_rot_matrix, phi_box_after_phi_rot) + np.tile(np.array([x, y, z]), [8,1]).T
        phi_box_final
        # print("phi_box_final = {}".format(phi_box_final))
        # print("{}".format(phi_box_final))

        face_i = np.array([7, 0, 0, 0, 4, 4, 6, 6, 4, 0, 3, 2])
        face_j = np.array([3, 4, 1, 2, 5, 6, 5, 2, 0, 1, 6, 3])
        face_k = np.array([0, 7, 2, 3, 6, 7, 1, 1, 5, 5, 7, 6])
        # Add the box representing theta assembly
        data_list.append(go.Mesh3d(
            # 8 vertices of a cube
            # x=np.array([theta_box_a[0],theta_box_b[0],theta_box_c[0],theta_box_d[0],theta_box_a[0],theta_box_b[0],theta_box_c[0],theta_box_d[0]]),
            # y=np.array([theta_box_a[1],theta_box_b[1],theta_box_c[1],theta_box_d[1],theta_box_a[1],theta_box_b[1],theta_box_c[1],theta_box_d[1]]),
            # z=np.array([theta_box_center_z - theta_box_h*0.5, theta_box_center_z - theta_box_h*0.5, theta_box_center_z - theta_box_h*0.5, theta_box_center_z - theta_box_h*0.5,
            #             theta_box_center_z + theta_box_h*0.5, theta_box_center_z + theta_box_h*0.5, theta_box_center_z + theta_box_h*0.5,theta_box_center_z + theta_box_h*0.5]),
            x = theta_box_final[0, :],
            y = theta_box_final[1, :],
            z = theta_box_final[2, :],
            i = [7, 0, 0, 0, 4, 4, 6, 6, 4, 0, 3, 2],
            j = [3, 4, 1, 2, 5, 6, 5, 2, 0, 1, 6, 3],
            k = [0, 7, 2, 3, 6, 7, 1, 1, 5, 5, 7, 6],
            opacity=0.1,
            color='#DC143C',
            flatshading = True
        ))

        if stl_outupt:
            if vertices_list is None:
                vertices_list = theta_box_final
                faces_list = np.array([face_i, face_j, face_k])
            else:
                ind_offset = vertices_list.shape[1]
                vertices_list = np.hstack((vertices_list, theta_box_final))
                faces_list = np.hstack((faces_list, np.array([face_i+ind_offset, face_j+ind_offset, face_k+ind_offset])))

        # Add the box representing phi assembly
        data_list.append(go.Mesh3d(
            # 8 vertices of a cube
            # x=np.array([theta_box_a[0],theta_box_b[0],theta_box_c[0],theta_box_d[0],theta_box_a[0],theta_box_b[0],theta_box_c[0],theta_box_d[0]]),
            # y=np.array([theta_box_a[1],theta_box_b[1],theta_box_c[1],theta_box_d[1],theta_box_a[1],theta_box_b[1],theta_box_c[1],theta_box_d[1]]),
            # z=np.array([theta_box_center_z - theta_box_h*0.5, theta_box_center_z - theta_box_h*0.5, theta_box_center_z - theta_box_h*0.5, theta_box_center_z - theta_box_h*0.5,
            #             theta_box_center_z + theta_box_h*0.5, theta_box_center_z + theta_box_h*0.5, theta_box_center_z + theta_box_h*0.5,theta_box_center_z + theta_box_h*0.5]),
            x = phi_box_final[0, :],
            y = phi_box_final[1, :],
            z = phi_box_final[2, :],
            i = [7, 0, 0, 0, 4, 4, 6, 6, 4, 0, 3, 2],
            j = [3, 4, 1, 2, 5, 6, 5, 2, 0, 1, 6, 3],
            k = [0, 7, 2, 3, 6, 7, 1, 1, 5, 5, 7, 6],
            opacity=0.1,
            color='#53B8BB',
            flatshading = True
        ))

        zbox1_final = zbox1_corners + np.tile(np.array([x, y, z]), [8,1]).T
        zbox2_final = zbox2_corners + np.tile(np.array([x, y, 0]), [8,1]).T

#commented out to not visualize z boxes
        # # Add the two boxes representing z assembly
        # data_list.append(go.Mesh3d(
        #     x = zbox1_final[0, :],
        #     y = zbox1_final[1, :],
        #     z = zbox1_final[2, :],
        #     i = [7, 0, 0, 0, 4, 4, 6, 6, 4, 0, 3, 2],
        #     j = [3, 4, 1, 2, 5, 6, 5, 2, 0, 1, 6, 3],
        #     k = [0, 7, 2, 3, 6, 7, 1, 1, 5, 5, 7, 6],
        #     opacity=0.1,
        #     color='#C0C0C0',
        #     flatshading = True
        # ))

        # data_list.append(go.Mesh3d(
        #     x = zbox2_final[0, :],
        #     y = zbox2_final[1, :],
        #     z = zbox2_final[2, :],
        #     i = [7, 0, 0, 0, 4, 4, 6, 6, 4, 0, 3, 2],
        #     j = [3, 4, 1, 2, 5, 6, 5, 2, 0, 1, 6, 3],
        #     k = [0, 7, 2, 3, 6, 7, 1, 1, 5, 5, 7, 6],
        #     opacity=0.1,
        #     color='#C0C0C0',
        #     flatshading = True
        # ))

        if stl_outupt:
            if vertices_list is None:
                vertices_list = phi_box_final
                faces_list = np.array([face_i, face_j, face_k])
            else:
                ind_offset = vertices_list.shape[1]
                vertices_list = np.hstack((vertices_list, phi_box_final))
                faces_list = np.hstack((faces_list, np.array([face_i+ind_offset, face_j+ind_offset, face_k+ind_offset])))

#commented out to not include z boxes
#        if stl_outupt:
#            if vertices_list is None:
#                vertices_list = zbox1_final
#                faces_list = np.array([face_i, face_j, face_k])
#            else:
#                ind_offset = vertices_list.shape[1]
#                vertices_list = np.hstack((vertices_list, zbox1_final))
#                faces_list = np.hstack((faces_list, np.array([face_i+ind_offset, face_j+ind_offset, face_k+ind_offset])))

#           if vertices_list is None:
#                vertices_list = zbox2_final
#                faces_list = np.array([face_i, face_j, face_k])
#            else:
#                ind_offset = vertices_list.shape[1]
#                vertices_list = np.hstack((vertices_list, zbox2_final))
#                faces_list = np.hstack((faces_list, np.array([face_i+ind_offset, face_j+ind_offset, face_k+ind_offset])))

        counter = counter + 1
        # if (counter > 15):
        #     break

    # Not very useful, commented out for now
    # fig_path_only = go.Figure(data=data_list[0])
    # fig_path_only.update_xaxes(range=[-150.0, 150.0], fixedrange=True)
    # fig_path_only.update_yaxes(range=[-60, 100], fixedrange=True)
    # fig_path_only.update_layout(width=int(800))
    # fig_path_only.update_layout(height=int(400))

    # fig_path_only.show()

    print("Number of configurations: {}".format(len(x_mm)))
    print("Number of traces: {}".format(len(data_list)))

    if stl_outupt:
        export_to_stl(vertices_list.T, faces_list.T, stl_filename)

    fig = go.Figure(data=data_list)
    fig.update_xaxes(range=[-150.0, 150.0], fixedrange=True)
    fig.update_yaxes(range=[-60, 100], fixedrange=True)
    fig.update_layout(width=int(700))
    fig.update_layout(height=int(600))

    fig.show()


In [ ]:
#@title *** New function for looking up configuration corresponding to visualized boxes ***
#############################
# Change this number here after running the code cell
#############################

def trace_to_config(trace_id: int) -> np.ndarray:
  trace_id = 472

  import math
  config_ind = math.floor((trace_id - 1) / 2)
  print(config_ind)
  configuration = np.array([x_mm[config_ind], y_mm[config_ind], z_mm[config_ind], theta_rad[config_ind], phi_rad[config_ind]])
  print("Configuration corresponding to trace id {} is {}".format(trace_id, configuration))
  return configuration

# Path visualizations

In [ ]:
#@title Visualizing shaping path (Note: this is for a left hand ONLY, x origin is near the middle finger position, so expect the actual range of motion required for both hands to be mirroring what's shown here)
import json

# Visualizing Shaping path
path_json = open(datasets[dataset_name]['shaping'])
shaping_path = json.load(path_json)
# print(shaping_path.keys())
x_mm = shaping_path['x']
y_mm = shaping_path['y']
z_mm = shaping_path['z']
theta_rad = shaping_path['theta']
phi_rad = shaping_path['phi']

if 'p_idm_0' in shaping_path:
  p_idm_0 = shaping_path['p_idm_0']
else:
  p_idm_0 = datasets[dataset_name]['p_idm_0']

print("using p_idm_0 = {}".format(p_idm_0))

# remove first 5 points, the random initial position in the middle of the hand...
x_mm = x_mm[5:]
y_mm = y_mm[5:]
z_mm = z_mm[5:]
theta_rad = theta_rad[5:]
phi_rad = phi_rad[5:]

visualize_path(x_mm, y_mm, z_mm, theta_rad, phi_rad,\
               stl_outupt=output_stl, stl_filename="shaping.stl", p_idm_0=p_idm_0)

using p_idm_0 = [0.0, 0.0, 0.0, 0.0, 0.0]
Gantry X range: [-80.4190701450955, 87.07693972995662]
Gantry Y range: [-89.50601549280539, 34.997885387167585]
Gantry Z range: [-10.056427019186746, 10.908820402619524]
Gantry THETA range: [-0.1998862815271736, 0.1998862815271736]
Gantry PHI range: [0.6997775066389149, 1.9999730854805142]
Number of configurations: 183
Number of traces: 367


In [ ]:
#@title Application path
# Visualizing Application path
path_json = open(datasets[dataset_name]['application'])
app_path = json.load(path_json)
x_mm = app_path['x']
y_mm = app_path['y']
z_mm = app_path['z']
theta_rad = app_path['theta']
phi_rad = app_path['phi']

if 'p_idm_0' in app_path:
  p_idm_0 = app_path['p_idm_0']
else:
  p_idm_0 = datasets[dataset_name]['p_idm_0']

print("using p_idm_0 = {}".format(p_idm_0))

visualize_path(x_mm, y_mm, z_mm, theta_rad, phi_rad,\
               stl_outupt=output_stl, stl_filename="application.stl", p_idm_0=p_idm_0)

using p_idm_0 = [0.0, 0.0, 0.0, 0.0, 0.0]
Gantry X range: [-81.50581433624544, 86.57728722827848]
Gantry Y range: [-112.94045192955556, -4.772998077406335]
Gantry Z range: [-16.83889242955774, 19.581514884374158]
Gantry THETA range: [-0.20988817279388586, 0.0871376890660537]
Gantry PHI range: [0.8350229670566283, 2.2852669920333026]
Number of configurations: 1587
Number of traces: 3175


In [ ]:
#@title Removal path
# Visualizing Removal path
path_json = open(datasets[dataset_name]['removal'])
removal_path = json.load(path_json)
x_mm = removal_path['x']
y_mm = removal_path['y']
z_mm = removal_path['z']
theta_rad = removal_path['theta']
phi_rad = removal_path['phi']

if 'p_idm_0' in removal_path:
  p_idm_0 = removal_path['p_idm_0']
else:
  p_idm_0 = datasets[dataset_name]['p_idm_0']

print("using p_idm_0 = {}".format(p_idm_0))


visualize_path(x_mm, y_mm, z_mm, theta_rad, phi_rad,\
               stl_outupt=output_stl, stl_filename="removal.stl", p_idm_0=p_idm_0)

using p_idm_0 = [0.0, 0.0, 0.0, 0.0, 0.0]
Gantry X range: [-77.29624200960717, 82.24280177622069]
Gantry Y range: [-124.07334692969148, -3.998000966899636]
Gantry Z range: [-31.223871520576502, 32.9109173902305]
Gantry THETA range: [-0.16457657447953794, 0.10259515738733627]
Gantry PHI range: [-1.4136851360080387, 3.287159979903826]
Number of configurations: 774
Number of traces: 1549


In [ ]:
#@title Cuticle path
# Visualizing Cuticle path
path_json = open(datasets[dataset_name]['cuticle'])
cuticle_path = json.load(path_json)
x_mm = cuticle_path['x']
y_mm = cuticle_path['y']
z_mm = cuticle_path['z']
theta_rad = cuticle_path['theta']
phi_rad = cuticle_path['phi']

if 'p_idm_0' in cuticle_path:
  p_idm_0 = cuticle_path['p_idm_0']
else:
  p_idm_0 = datasets[dataset_name]['p_idm_0']

print("using p_idm_0 = {}".format(p_idm_0))


visualize_path(x_mm, y_mm, z_mm, theta_rad, phi_rad,\
               stl_outupt=output_stl, stl_filename="cuticle.stl", p_idm_0=p_idm_0)

using p_idm_0 = [0.0, 0.0, 0.0, 0.0, 0.0]
Gantry X range: [-68.30249697940077, 79.07000839056454]
Gantry Y range: [-112.9650550124288, -16.397954735006817]
Gantry Z range: [-14.486755958871717, 30.89200167724891]
Gantry THETA range: [-0.16457657447953794, 0.10259515738733627]
Gantry PHI range: [0.9749784683844113, 1.8151600516758777]
Number of configurations: 1231
Number of traces: 2463
